# Operator splitting 

In [10]:
import numpy as np
import matplotlib.pyplot as plt
plt.style.use('seaborn-v0_8-whitegrid')

import matplotlib as mpl
mpl.rc('lines', linewidth=2)

from nm_lib import nm_lib as nm

## 1- OS precision

Solve the following Burgers' equation: 

$$\frac{\partial u}{\partial t} = - a \frac{\partial u}{\partial x} - b \frac{\partial u}{\partial x}   \tag{1}$$

following exersize [2b](https://github.com/AST-Course/AST5110/blob/main/ex_2b.ipynb). where $x[x_0, x_f]$ with $x_0 = −2.6$, $x_f = 2.6$, $a=-0.7$ and $b=-0.3$, periodic boundary conditions and with initial condition:

$$u(x,t=t_0) = \cos^2 \left(\frac{6 \pi x}{5} \right) / \cosh(5x^2)  \tag{2}$$

Solve the evolution for the following four different approaches: 

- 1 With additive OS.  

- 2 With Lie-Trotter OS. 

- 3 With Strang OS.

- 4 Without an operator splitting and single time-step method but add the to terms: 

$$\frac{\partial u}{\partial t} = - (a+b) \frac{\partial u}{\partial x}$$

for $nump=256$ and 100 steps.

_Suggestion_: use the Lax-method scheme for all cases with `deriv_cent`. Make sure the boundaries are properly selected.

Fill in the function `osp_LL_Add`, `osp_LL_Lie`, and `osp_LL_Strang`.

Start with $cfl\_cut = 0.4$ and increase up to $0.9$.  

Which OS schemes are stable? Which one is more diffusive? Why?

In [11]:
def u_0(x: np.ndarray, t: float = 0) -> np.ndarray:
    r"""
    Initial condition for the advection equation.

    Parameters
    ----------
    x : `array`
        the x-axis.
    t : `float`
        the time.
    
    Returns
    -------
    `array`
        the initial condition.
    """
    return np.cos(6*np.pi*x / 5)**2 / np.cosh(5*x**2)

In [12]:
x0 = -2.6
xf = 2.6
a = -0.7
b = -0.3

nump = 256 # number of grid points

# xx = np.linspace(x0, xf, nump)

xx = np.arange(nump) / (nump - 1.0) * (xf - x0) + x0

In [13]:
nt = 200
cfl_cut = 0.4

t_Add, unnt_Add = nm.ops_Lax_LL_Add(xx, u_0(xx), nt=nt, a=a, b=b, cfl_cut=cfl_cut, ddx=nm.deriv_cent, bnd_limits=[1, 1])
t_Lie, unnt_Lie = nm.ops_Lax_LL_Lie(xx, u_0(xx), nt=nt, a=a, b=b, cfl_cut=cfl_cut, ddx=nm.deriv_cent, bnd_limits=[1, 1])
t_Strang, unnt_LL_Strang = nm.ops_Lax_LL_Strang(xx, u_0(xx), nt=nt, a=a, b=b, cfl_cut=cfl_cut, ddx=nm.deriv_cent, bnd_limits=[1, 1])
t_ab, unnt_ab = nm.evolv_Lax_adv_burgers(xx, u_0(xx), nt=nt, a=a+b, cfl_cut=cfl_cut, ddx=nm.deriv_cent, bnd_limits=[1, 1])

In [14]:
# Find the similar timesteps for animation

atol = 1e-1
similar = np.where(np.isclose(t_Add, t_Lie, atol=atol))[0]
similar = np.where(np.isclose(t_Add[similar], t_Strang, atol=atol))[0]
# Setting tolerance for a+b a little bigger to get some frames of Add blowing up
similar = np.where(np.isclose(t_Add[similar], t_ab, atol=2e-1))[0] 

print(similar.shape)

(58,)


In [15]:
# Setup for animation
from matplotlib import animation
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

def init(): 
    axes.plot(xx,unnt_Add[:,0], label='Add')
    axes.plot(xx,unnt_Lie[:,0], label='Lie')
    axes.plot(xx,unnt_LL_Strang[:,0], label='LL_Strang')
    axes.plot(xx,unnt_ab[:,0], label='Lax (a+b)')
    axes.legend(loc='upper right', frameon=True, framealpha=0.5)

def animate(i):
    axes.clear()
    axes.plot(xx,unnt_Add[:,similar[i]], label='Add')
    axes.plot(xx,unnt_Lie[:,similar[i]], label='Lie')
    axes.plot(xx,unnt_LL_Strang[:,similar[i]], label='LL_Strang')
    axes.plot(xx,unnt_ab[:,similar[i]], label='Lax (a+b)')
    axes.set_title('t≈%.2f'%t_Lie[similar[i]])
    axes.legend(loc='upper right', frameon=True, framealpha=0.5)
    axes.set_ylim(-0.05, 1.05)

fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(7, 3))
anim = FuncAnimation(fig, animate, interval=50, frames=len(similar), init_func=init)
plt.close()
HTML(anim.to_jshtml())

<span style="color:#78AE7E">

Above is a comparison of the four different methods over time, when `cfl_cut=0.4`. We see that the Add method is the only one to blow up, beginning at around $t=0.35$. 

The Lie, Strang and Lax method with $a+b$ added do not blow up during the course of the simulation, but we see them diffuse as time passes.
The Strang method diffuses the quickest, then the Lie method and the Add method. The Lax method with $a+b$ added is the least diffusive method. 

The four solutions move across the simulated span at different paces, due to the difference in the coefficients $a$ and $b$. The solution that moves the fastest is the Lie method, then the Add method, then the Strang method and finally the Lax method with $a+b$ added.
<span>

<span style="color:pink"> JMS, ok, now I'm pink, blue, red, yellow and orange :-). </span>.

<span style="color:blue"> No you understood better and fixed most of the bugs. You are correct that Strang method is second order.  but ... :-)</span>.

<span style="color:red"> The time shown in each of the cases is different. You should try to match the same instant so it will make the comparison easier. This may change some of your conclusions. Note that `similar` is not doing the job that you want to do.</span>.


In [7]:
nt = 100
cfl_cut = 0.9

t_Add, unnt_Add = nm.ops_Lax_LL_Add(xx, u_0(xx), nt=nt, a=a, b=b, cfl_cut=cfl_cut, ddx=nm.deriv_cent, bnd_limits=[1, 1])
t_Lie, unnt_Lie = nm.ops_Lax_LL_Lie(xx, u_0(xx), nt=nt, a=a, b=b, cfl_cut=cfl_cut, ddx=nm.deriv_cent, bnd_limits=[1, 1])
t_Strang, unnt_LL_Strang = nm.ops_Lax_LL_Strang(xx, u_0(xx), nt=nt, a=a, b=b, cfl_cut=cfl_cut, ddx=nm.deriv_cent, bnd_limits=[1, 1])
t_ab, unnt_ab = nm.evolv_Lax_adv_burgers(xx, u_0(xx), nt=nt, a=a+b, cfl_cut=cfl_cut, ddx=nm.deriv_cent, bnd_limits=[1, 1])

In [8]:
# Find the similar timesteps for animation

atol = 1e-1
similar = np.where(np.isclose(t_Add, t_Lie, atol=atol))[0]
similar = np.where(np.isclose(t_Add[similar], t_Strang, atol=atol))[0]
# Setting tolerance for a+b a little bigger to get some frames of Add blowing up
similar = np.where(np.isclose(t_Add[similar], t_ab, atol=3e-1))[0] 

print(similar.shape)

(39,)


In [9]:
fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(7, 3))
anim = FuncAnimation(fig, animate, interval=50, frames=len(similar), init_func=init)
plt.close()
HTML(anim.to_jshtml())

<span style="color:#78AE7E">

In the case where `cfl_cut=0.9`, we see that the amplitude of the Lie method begins to increase immediately, indicating that it is an unstable solution for this case. The Lie method later begins to oscillate and blow up at around $t=1$. The Add method diffuses, but blows up at $t=0.81$. 

As with `cfl_cut=0.4`, the Strang and Lax methods are stable solutions, and they behave in the same way. Here it is even clearer that the Lax method with $a+b$ added diffuses the least, and the Strang method diffuses the most. 

<span>

<span style="color:pink"> JMS. </span>.

<span style="color:orange"> I think after addressing my comments above some of the conclusions here may change</span>.

## 2- When does it not work? 

Use OS-Strang from the previous exercise and try to apply a predictor-corrector explicit method. 
To facilitate this exercise, `nm_lib` already includes the predictor-corrector Hyman method, which is included Bifrost (`Hyman`). Fill in the function `osp_Lax_LH_Strang`. Use the same setup as the previous exercise but with $nump=512$, $500$ steps, and $cfl\_cut=0.8$. 

What do you notice? 

__Optional__: Apply the Hyman predictor-corrector explicit method to the Burgers equation and check if the following is true: 

$$u^{n+1} = F\, u^{n}\Delta t \approx G\, u^{n}\Delta t+H\, u^{n}\Delta t$$

In [10]:
x0 = -2.6
xf = 2.6
a = -0.7
b = -0.3

nump = 512 # number of grid points
nt = 500 
# nt = 10
cfl_cut = 0.8

xx = np.linspace(x0, xf, nump)

t_LH, unnt = nm.ops_Lax_LH_Strang(xx, u_0(xx), nt=nt, a=a, b=b, cfl_cut=cfl_cut, ddx=nm.deriv_cent, bnd_limits=[1, 1])
t_LL, unnt_LL = nm.ops_Lax_LL_Strang(xx, u_0(xx), nt=nt, a=a, b=b, cfl_cut=cfl_cut, ddx=nm.deriv_cent, bnd_limits=[1, 1])

In [11]:
# Find the similar timesteps for animation

atol = 1e-1
similar = np.where(np.isclose(t_LH, t_LL, atol=atol))[0]

print(similar.shape)

(35,)


In [12]:
def init(): 
    axes.plot(xx,unnt[:,0], label='LH')
    axes.plot(xx,unnt_LL[:,0], label='LL')
    axes.legend(loc='upper right', frameon=True, framealpha=0.5)

def animate(i):
    axes.clear()
    axes.plot(xx,unnt[:,similar[i]], label='LH')
    axes.plot(xx,unnt_LL[:,similar[i]], label='LL')
    axes.set_title(f't_LH={t_LH[similar[i]]:.2f}, t_LL={t_LL[similar[i]]:.2f}')
    axes.set_ylim(-0.05, 1.05)
    axes.legend(loc='upper right', frameon=True, framealpha=0.5)

fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(7, 3))
anim = FuncAnimation(fig, animate, interval=30, frames=len(similar), init_func=init)
plt.close()
HTML(anim.to_jshtml())

<span style="color:#78AE7E">

Here we have compared the Strang method with (LH) and without (LL) the Hyman predictor-corrector method. Both solutions are stable, as is expected. 

We can see, however, that the Hyman method seems to be moving ahead of the LL-method. But this could be a result of the difference in timesteps for the two methods. My current method for finding common timepoints is not fool-proof, and there are very few timepoints that are close to being common for both methods.
<span>

<span style="color:pink"> JMS. </span>.

<span style="color:blue"> I think your implementation for the LH is correct. However: </span>.

<span style="color:orange"> I think after addressing my comments above some of the conclusions here may chang </span>.


<span style="color:pink"> JMS. </span>.

<span style="color:blue"> Nice comparison, but when there is a phase error it is harder to compare since the number of steps will be different. Once you correct this, I'll give a more detailed description of the Hyman method. </span>.